# 
Application Level Scheduling

RADICAL-Pilot (RP) by default uses its internal scheduler to efficiently place tasks on the available cluster resources.  Some use cases however require more fine grained and/or explicit control over task placement.  RP supports that functionality with *__application level scheduling__*.  In that case the pilot will report about the available nodes and resources, but will leave it to the application to assign resources to the tasks.  A number of API functions are provided to simplify the development of such application level schedulers, and this tutorial will demonstrate their use.

<div class="alert alert-info">

__Note:__ At the moment it is not possible to mix application level scheduling and RP's internal scheduling in the same session.
__Note:__ Application level scheduling is only supported for executable tasks, RAPTOR tasks will ignore any related settings.
__Note:__ The outputs of the various cells above may differ, depending on your localhost's hardware configuration.

</div>


## Notation

The following terms will be used throughout this tutorial:

  - *__task:__* an exectable piece of work comprised of one or more processes, all running the same executable on a dedicated set of resources.
  - *__rank:__* one of theprocesses which comprise a running task.  The term _rank_ is frequently used for MPI applications, but we use it generically for any task which uses multiprocessing.
  - *__slot:__* the set of resources which are assigned to a single _rank_, i.e., to a single task process. Note that each _rank_ can utilize multiple cores and/or GPUs, usually by support of libraries and frameworks such as OpenMP, CUDA, OpenCL etc.
  - *__occupation:__* the portion of a resource assigned to a _rank_.  For example, two ranks could share a GPU, and then each of the ranks would get `occupation=0.5` assigned for that GPU.



## Pilot Resources

We will first start a normal RP session and submit a pilot.  We then wait for the pilot to become active and inspect its resources by retrieving its nodelist which at that point will be available.

In [1]:
import radical.pilot as rp
import pprint

In [2]:
session = rp.Session()

pmgr = rp.PilotManager(session)
tmgr = rp.TaskManager(session)

pilot = pmgr.submit_pilots(rp.PilotDescription(
    {'resource': 'local.localhost',
     'runtime' : 60,
     'nodes'   : 4}))

tmgr.add_pilots(pilot)
pilot.wait([rp.PMGR_ACTIVE, rp.FAILED])

assert pilot.state == rp.PMGR_ACTIVE

nodelist = pilot.nodelist
print('got %d nodes' % len(nodelist.nodes))

new session: [rp.session.thinkie.merzky.020128.0005]                           \
[tcp://10.0.0.39:10001]                                          ok
create pilot manager                                                          ok
create task manager                                                           ok
submit 1 pilot(s)
                        oklhost           4 nodes


got 4 nodes


The nodelist (type: `rp.NodeList`) has the following attributes:

  - `uniform`: boolean, indicates if the nodes have identical resources
  - `cores_per_node`, `gpus_per_node`, `mem_per_node`, `lfs_per_node`: amount of resources per node.  Those attributes will be `None` for non-uniform nodelists.
  - `nodes`: the actual list of nodes.

Let's inspect one of the nodes (`nodeslist.nodes[0]`).  A node in the nodelist has the type `rp.NodeResource` with the following attributes:

  - `index`: unique node identifier used within RP
  - `name`: hostname (does not need to be unique!)
  - `mem`: available memory (in MB)
  - `lfs`: available disk storage (in MB)
  - `cores`: available CPU cores and their occupation
  - `gpus`: available GPUs and their occupation.

The core and gpu information are constructed of an integer (the resource index) and a float (the resource occupation where `0.0` is *not used* and `1.0` is *fully used*).

In [3]:
# inspect one node
print('#nodes: ', len(nodelist.nodes))

node = nodelist.nodes[0]
pprint.pprint(node.as_dict())


#nodes:  4
{'cores': [{'index': 0, 'occupation': 0.0},
           {'index': 1, 'occupation': 0.0},
           {'index': 2, 'occupation': 0.0},
           {'index': 3, 'occupation': 0.0},
           {'index': 4, 'occupation': 0.0},
           {'index': 5, 'occupation': 0.0},
           {'index': 6, 'occupation': 0.0},
           {'index': 7, 'occupation': 0.0},
           {'index': 8, 'occupation': 0.0},
           {'index': 9, 'occupation': 0.0},
           {'index': 10, 'occupation': 0.0},
           {'index': 11, 'occupation': 0.0}],
 'gpus': [{'index': 0, 'occupation': 0.0}],
 'index': 0,
 'lfs': 1000000,
 'mem': 65536,
 'name': 'localhost'}


Based on that information we can now define _slots_, i.e., sets of resources for task ranks to run on. The slot for the simplest possible task (in RP) would just allocate one core.  Let's create two slots (core ID 3 and 4) for a two-ranked task which runs `radical-pilot-hello.sh` - that is a script which will report the resources used by the task:


In [4]:
slot_1 = rp.Slot(node_index=0, node_name='localhost', cores=[3])
slot_2 = rp.Slot(node_index=0, node_name='localhost', cores=[4])

td_1 = rp.TaskDescription({'executable': 'radical-pilot-hello.sh', 
                           'arguments' : [1],
                           'ranks'     : 2,
                           'slots'     : [slot_1, slot_2]})
task_1 = tmgr.submit_tasks(td_1)
tmgr.wait_tasks(uids=task_1.uid)
pprint.pprint(task_1.slots)
print(task_1.stdout)

submit: ########################################################################
wait  : ########################################################################
	DONE      :     1
                                                                              ok


[{'cores': [{'index': 3, 'occupation': 1.0}],
  'gpus': [],
  'lfs': 0,
  'mem': 0,
  'node_index': 0,
  'node_name': 'localhost',
  'version': 1},
 {'cores': [{'index': 4, 'occupation': 1.0}],
  'gpus': [],
  'lfs': 0,
  'mem': 0,
  'node_index': 0,
  'node_name': 'localhost',
  'version': 1}]
0 : PID     : 318349
0 : NODE    : thinkie
0 : CPUS    : 00000000000000000011
0 : GPUS    : 00
0 : RANK    : 0
0 : THREADS : 1
0 : SLEEP   : 1
1 : PID     : 318355
1 : NODE    : thinkie
1 : CPUS    : 00000000000000001100
1 : GPUS    : 00
1 : RANK    : 1
1 : THREADS : 1
1 : SLEEP   : 1
stress-ng: info:  [318415] setting to a 1 sec run per stressor
stress-ng: info:  [318418] setting to a 1 sec run per stressor
stress-ng: info:  [318418] dispatching hogs: 1 cpu
stress-ng: info:  [318415] dispatching hogs: 1 cpu
stress-ng: info:  [318418] skipped: 0
stress-ng: info:  [318418] passed: 1: cpu (1)
stress-ng: info:  [318418] failed: 0
stress-ng: info:  [318418] metrics untrustworthy: 0
stress-ng: info: 

A simpler way to obtain task slots is to let the node's `NodeResource` find it for you.  That will return a viable slot, or `None` if the requested resources are not available at this moment.

In [5]:
rr = rp.RankRequirements(n_cores=1)
slot_3 = node.find_slot(rr)
assert(slot_3)
pprint.pprint(slot_3.as_dict())

{'cores': [{'index': 0, 'occupation': 1.0}],
 'gpus': [],
 'lfs': 0,
 'mem': 0,
 'node_index': 0,
 'node_name': 'localhost',
 'version': 1}


If we now check the node, we will see that the resource occupation of the first core changed.

In [6]:
pprint.pprint(node.as_dict())

{'cores': [{'index': 0, 'occupation': 1.0},
           {'index': 1, 'occupation': 0.0},
           {'index': 2, 'occupation': 0.0},
           {'index': 3, 'occupation': 0.0},
           {'index': 4, 'occupation': 0.0},
           {'index': 5, 'occupation': 0.0},
           {'index': 6, 'occupation': 0.0},
           {'index': 7, 'occupation': 0.0},
           {'index': 8, 'occupation': 0.0},
           {'index': 9, 'occupation': 0.0},
           {'index': 10, 'occupation': 0.0},
           {'index': 11, 'occupation': 0.0}],
 'gpus': [{'index': 0, 'occupation': 0.0}],
 'index': 0,
 'lfs': 1000000,
 'mem': 65536,
 'name': 'localhost'}


We can also register our manually created slots as occupied so that later calls to `find_slot` will take that information into account (after use, a slot should be deallocated again).

In [7]:
node.allocate_slot(slot_1)
node.allocate_slot(slot_2)
pprint.pprint(node.as_dict())

{'cores': [{'index': 0, 'occupation': 1.0},
           {'index': 1, 'occupation': 0.0},
           {'index': 2, 'occupation': 0.0},
           {'index': 3, 'occupation': 1.0},
           {'index': 4, 'occupation': 1.0},
           {'index': 5, 'occupation': 0.0},
           {'index': 6, 'occupation': 0.0},
           {'index': 7, 'occupation': 0.0},
           {'index': 8, 'occupation': 0.0},
           {'index': 9, 'occupation': 0.0},
           {'index': 10, 'occupation': 0.0},
           {'index': 11, 'occupation': 0.0}],
 'gpus': [{'index': 0, 'occupation': 0.0}],
 'index': 0,
 'lfs': 1000000,
 'mem': 65536,
 'name': 'localhost'}


To allocate a larger set of slots, for example for multi-rank tasks, RP can search the node list itself for available resources.  That search might return slots which are distributed across all nodes.  For example, the call below will allocate the resources for 4 ranks where each rank uses 4 cores and half a GPU (2 ranks can share one GPU).  As the GPU is the limiting resource in this scenario, we will be able to place at most 2 ranks per node:

In [8]:
rr = rp.RankRequirements(n_cores=4, n_gpus=1, gpu_occupation=0.5)
slots = nodelist.find_slots(rr, n_slots=4)
for slot in slots:
    print('index:', slot.node_index, 'cores:', slot.cores, 'gpus:', slot.gpus)

index: 0 cores: [RO: 1:1.00, RO: 2:1.00, RO: 5:1.00, RO: 6:1.00] gpus: [RO: 0:0.50]
index: 0 cores: [RO: 7:1.00, RO: 8:1.00, RO: 9:1.00, RO: 10:1.00] gpus: [RO: 0:0.50]
index: 1 cores: [RO: 0:1.00, RO: 1:1.00, RO: 2:1.00, RO: 3:1.00] gpus: [RO: 0:0.50]
index: 1 cores: [RO: 4:1.00, RO: 5:1.00, RO: 6:1.00, RO: 7:1.00] gpus: [RO: 0:0.50]


## Application Level Scheduling

With the above tools, the simplest implementation of an application level scheduler would be:


In [ ]:
import threading as mt

class AppScheduler(object):

    def __init__(self, tmgr, nodelist):
        '''
        tmgr    : task manager which handles execution of tasks
        nodelist: resources to be used for task execution
        '''
        self._tmgr            = tmgr
        self._nodelist        = nodelist
        self._running_tasks   = dict()
        self._completed_tasks = list()
        self._lock            = mt.Lock()
        
        self._tmgr.register_callback(self._state_cb)

    def _state_cb(task, state):
        if state in rp.FINAL:
            assert state == rp.DONE
            self._finalize_task(task)

    def _finalize_task(self, task):
        if task.uid in self._running_tasks:
            del self._running_tasks[task.uid]
            self._completed_tasks.append(task)

    def wait_tasks(self, uids=None, timeout=0.0):
        if not uids:
            uids = list(self._running_tasks.keys()) 
        return self._tmgr.wait_tasks(uids=uids, timeout=timeout)
        
    def submit(self, tds):
        '''
        tds: list of rp.TaskDescriptions - list of tasks to run
        '''

        while tds:

            # find slots for all task descriptions
            allocated = list()
            not_allocated = list()

            for td in tds:
                rr = rp.RankRequirements(n_cores=td.cores_per_rank, n_gpus=td.gpus_per_rank, 
                                         mem=td.mem_per_rank,  lfs=td.lfs_per_rank)
                slots = nodelist.find_slots(rr, n_slots=td.ranks)
                if slots:
                    # this task can be submitted
                    td.slots = slots
                    allocated.append(td)
                else:
                    # this task has to be retries later on
                    not_allocated.append(td)

            # submit all tasks for which resources were found
            submitted = tmgr.submit_tasks(allocated)
            for task in submitted:
                self._running_tasks[task.uid] = task
                self._running_tasks[task.uid] = task
                print('submitted %s' % task.uid)

            if not_allocated:
                # could not submit all tasks - wait for resources to become available 
                # on and attempt to schedule the remaining tasks in the next iteration
                tds = not_allocated
            
                while True:
                    states = self.wait_tasks(timeout=1.0)
                    print(states)
                    
                    # if we got any free resources, try to schedule more tasks
                    if rp.DONE in states or rp.FAILED in states:
                        break
    
scheduler = AppScheduler(tmgr, nodelist)

tds = list()
for i in range(5):
    td = {'executable'     : 'sleep', 
          'arguments'      : [i + 5],
          'ranks'          : i + 1, 
          'cores_per_rank' : i + 1,
          'slots'          : slots}
    tds.append(rp.TaskDescription(td))

scheduler.submit(tds)
scheduler.wait_tasks()

submit: ########################################################################
wait  : 

submitted task.000001
submitted task.000002
submitted task.000003



	AGENT_EXECUTING:     3
                                                                         timeout
wait  : 

['AGENT_EXECUTING', 'AGENT_EXECUTING', 'AGENT_EXECUTING']



	AGENT_EXECUTING:     3
                                                                         timeout
wait  : 

...


	DONE      :     3
                                                                              ok
wait  : ########################################################################
	DONE      :     3
                                                                              ok
wait  : 

['DONE', 'DONE', 'DONE']
['DONE', 'DONE', 'DONE']


########################################################################
	DONE      :     3
                                                                              ok
wait  : ########################################################################
	DONE      :     3
                                                                              ok
wait  : 

['DONE', 'DONE', 'DONE']
['DONE', 'DONE', 'DONE']


#